In [1]:
%load_ext autoreload
%autoreload 2

import sys
sys.path.append('../')
sys.path.append('../resnet_model')

In [2]:
from utils.general.read_files import read_from_json
from utils.general.dataset_variables import TripletSegmentationVariables

VERBTARGET_DICT = TripletSegmentationVariables.categories['verbtarget']

In [3]:
from collections import defaultdict

def resolve_triplet_matching(issue_json_path, results_from_model_path):
    matched = {}
    unmatched = {}
       
    issues_dict = read_from_json(issue_json_path)
    model_outputs  = read_from_json(results_from_model_path) 

    # Group predictions by frame and instrument
    grouped_by_frame_instrument = defaultdict(lambda: defaultdict(list))
    total_real_matching_issues = 0 #These are the ones that actually required matching, usually graspers. 
    matching_problems_solved_amount  = 0

    # match with triplets. 
    for key, value in model_outputs.items():
        frame, instrument, cholecinstanceseg_instance_id, _, _ = key.split(",")
        vt_id = int(value['verbtarget']) + 1
        vt_name = VERBTARGET_DICT[str(vt_id)]
        grouped_by_frame_instrument[frame][instrument].append((cholecinstanceseg_instance_id, vt_name, key))

    for frame, instruments_info in grouped_by_frame_instrument.items():
        
        print(f'solving {frame} ==============================')
        vid_name = frame.split('_')[1]
        assert issues_dict[vid_name][f'{frame}.json']['reason'] == 'matching', 'a non-matching issue has slipped into your pipeline'
        cholecT50_triplet_names_annotations_for_frame = issues_dict[vid_name][f'{frame}.json']['triplet_classes'] # the triplets in the frames
        
        print(f'cholecT50_triplet_names_annotations_for_frame {cholecT50_triplet_names_annotations_for_frame}')
        
        
        
        unmatched_preds_this_frame = []  # collect all unmatched preds in this frame
        
        for instrument, preds in instruments_info.items():
            print(f'predicted verb targets for {instrument} is  {[pred_info[1] for pred_info in preds] }')
            if len(preds) == 1:
                # Only one instance, confident match
                _, _ , full_key = preds[0]   
                selected_triplet = next((item for item in cholecT50_triplet_names_annotations_for_frame if instrument in item), None) # make the triplet the default, since it is the only one.                             
                if selected_triplet:
                    matched[full_key] = selected_triplet
                    cholecT50_triplet_names_annotations_for_frame.remove(selected_triplet)
                    print(f'Removed default instrument, cholecT50_triplet_names_annotations_for_frame  {cholecT50_triplet_names_annotations_for_frame}')
                else:
                    raise ValueError('somethign is wrong with the algorithm, there should always be a triplet here. ')    
                
                
            else:
                
                # Multiple instances, try to match based on verbtarget
                if instrument != 'grasper': 
                    print(f'Wow!! for {frame} we had a {instrument} that caused the matching issue')
                 
                for instance_id, vt_name, full_key in preds:
                    total_real_matching_issues +=1
                    predicted_triplet =  f'{instrument},{vt_name}'
                    
                    if predicted_triplet in cholecT50_triplet_names_annotations_for_frame:
                        matching_problems_solved_amount += 1 
                        matched[full_key] = predicted_triplet
                        cholecT50_triplet_names_annotations_for_frame.remove(predicted_triplet)
                        
                        print(f'{full_key} matched') 
                        print(f'cholecT50_triplet_names_annotations_for_frame after matching {cholecT50_triplet_names_annotations_for_frame}')
                        
                    else: 
                        unmatched[full_key] = None 
                        unmatched_preds_this_frame.append((instrument, full_key, predicted_triplet))   
                        
                
        # 🔍 Final fallback matching by elimination
        # Filter grasper-only unmatched preds
            
        unmatched_grasper_preds = [(instr, key, triplet) for instr, key, triplet in unmatched_preds_this_frame if instr == 'grasper']
        unmatched_grasper_triplets = [t for t in cholecT50_triplet_names_annotations_for_frame if 'grasper' in t]

        if len(unmatched_grasper_preds) == 1 and len(unmatched_grasper_triplets) == 1:
            instr, key, _ = unmatched_grasper_preds[0]
            final_triplet = unmatched_grasper_triplets[0]
            matched[key] = final_triplet
            cholecT50_triplet_names_annotations_for_frame.remove(final_triplet)
            del unmatched[key]
            matching_problems_solved_amount += 1
            print(f'✅ Post-loop fallback match used for {key} → {final_triplet}')    
            print(f'cholecT50_triplet_names_annotations_for_frame after elimination {cholecT50_triplet_names_annotations_for_frame}')    
        
        # 🧹 Final pass: assign all unmatched using verb or target match
        still_unmatched_preds = [(instr, key, pred_triplet) for instr, key, pred_triplet in unmatched_preds_this_frame if key in unmatched]
        # remaining_triplets = cholecT50_triplet_names_annotations_for_frame[:]

        for instr, full_key, predicted_triplet in still_unmatched_preds:
            pred_instr, pred_verb, pred_target = predicted_triplet.split(',')
            

            # 1️⃣ Try verb match
            verb_match = next((
                gt_triplet for gt_triplet in cholecT50_triplet_names_annotations_for_frame
                if instr in gt_triplet and pred_verb in gt_triplet
            ), None)
            
            print(f'verb_match, {verb_match} for predicted_triplet {predicted_triplet}')
            print(f'cholecT50_triplet_names_annotations_for_frame before verbmatch {cholecT50_triplet_names_annotations_for_frame}')   
            
            if verb_match:
                matched[full_key] = verb_match
                cholecT50_triplet_names_annotations_for_frame.remove(verb_match)
                del unmatched[full_key]
                print(f'🟩 Verb match fallback for {full_key} → {verb_match}')
                matching_problems_solved_amount += 1
                continue
            
             

            # 2️⃣ Try target match
            target_match = next((
                gt_triplet for gt_triplet in cholecT50_triplet_names_annotations_for_frame
                if instr in gt_triplet and pred_target in gt_triplet
            ), None)
            
            print(f'target_match, {target_match}, for predicted_triplet {predicted_triplet}')
            print(f'cholecT50_triplet_names_annotations_for_frame before target_match {cholecT50_triplet_names_annotations_for_frame}')  
            
            if target_match:
                matched[full_key] = target_match
                cholecT50_triplet_names_annotations_for_frame.remove(target_match)
                del unmatched[full_key]
                print(f'🟨 Target match fallback for {full_key} → {target_match}')
                matching_problems_solved_amount += 1
                continue
                

            # 3️⃣ Final brute-force fallback (match anything with same instrument)
            print(f'need brute force match for for predicted_triplet {predicted_triplet}')
            print(f'cholecT50_triplet_names_annotations_for_frame before target_match {cholecT50_triplet_names_annotations_for_frame}') 
            
            instr_only_match = next((
                gt_triplet for gt_triplet in cholecT50_triplet_names_annotations_for_frame
                if instr in gt_triplet
            ), None)

            if instr_only_match:
                matched[full_key] = instr_only_match
                cholecT50_triplet_names_annotations_for_frame.remove(instr_only_match)
                del unmatched[full_key]
                print(f'🟥 Brute force fallback for {full_key} → {instr_only_match}')
                matching_problems_solved_amount += 1

    return matched, unmatched, total_real_matching_issues, matching_problems_solved_amount


In [4]:
issue_json_path = 'outputs/error_dict_between_extension_and_cholecT50_datasets.json'
results_from_model_path = '../resnet_model/work_dirs/parallel_decoder_prediction_cholecinstanceseg_extension_matching/results.json'
matched, unmatched, total_real_matching_issues, matching_problems_solved_amount =  resolve_triplet_matching(issue_json_path, results_from_model_path)

solving t50_VID02_000228 ==============================
cholecT50_triplet_names_annotations_for_frame ['grasper,retract,liver', 'grasper,null_verb,null_target']
predicted verb targets for grasper is  ['retract,liver', 'retract,liver']
t50_VID02_000228,grasper,1,None,None matched
cholecT50_triplet_names_annotations_for_frame after matching ['grasper,null_verb,null_target']
✅ Post-loop fallback match used for t50_VID02_000228,grasper,2,None,None → grasper,null_verb,null_target
cholecT50_triplet_names_annotations_for_frame after elimination []
solving t50_VID02_000234 ==============================
cholecT50_triplet_names_annotations_for_frame ['grasper,retract,liver', 'grasper,null_verb,null_target']
predicted verb targets for grasper is  ['grasp,specimen_bag', 'retract,liver']
t50_VID02_000234,grasper,2,None,None matched
cholecT50_triplet_names_annotations_for_frame after matching ['grasper,null_verb,null_target']
✅ Post-loop fallback match used for t50_VID02_000234,grasper,1,None,None 

In [5]:
total_real_matching_issues

10239

In [6]:
matching_problems_solved_amount

10239

In [ ]:
matched

In [8]:
from utils.general.save_files import save_to_json

matched_file_path = 'outputs/matched_tripletsegmentation_extension.json'

save_to_json(data=matched, json_file_path=matched_file_path)